In [12]:
from plotly.subplots import make_subplots

import json

import pandas as pd
import numpy as np
import datetime as dt
import plotly.graph_objects as go

In [23]:
with open("../results/BTCUSDT_candlestick.json",'r') as f:
    data = json.loads(f.read())
data = pd.json_normalize(data,record_path=['BTCUSDT'])

In [25]:
float_variables = ["OpenPrice","HighPrice","LowPrice","ClosePrice","Volume","QuoteAssetVolume"]
datetime_variables = ["openTime","closeTime"]

for i in range(len(float_variables)):
    data[float_variables[i]] = data[float_variables[i]].astype(float)

for i in range(len(datetime_variables)):
    data[datetime_variables[i]] = pd.to_datetime(data[datetime_variables[i]])

In [22]:
data.head()

openTime  OpenPrice  HighPrice  LowPrice  ClosePrice     Volume  \
0 2023-10-01 14:00:00   27192.04   27229.29  27083.24    27119.79  996.38542   
1 2023-10-01 15:00:00   27119.79   27155.85  27107.01    27153.18  541.59390   
2 2023-10-01 16:00:00   27153.17   27155.00  27082.38    27112.19  585.50462   
3 2023-10-01 17:00:00   27112.20   27140.45  27035.78    27072.35  730.04943   
4 2023-10-01 18:00:00   27072.34   27100.01  27065.07    27096.13  438.07759   

            closeTime  QuoteAssetVolume  nTrades  
0 2023-10-01 14:59:59      2.705339e+07    43790  
1 2023-10-01 15:59:59      1.469446e+07    29637  
2 2023-10-01 16:59:59      1.588032e+07    29652  
3 2023-10-01 17:59:59      1.977801e+07    34610  
4 2023-10-01 18:59:59      1.186694e+07    25812

In [26]:
fig = go.Figure(
    data=[go.Candlestick(x=data["openTime"],
                         open=data["OpenPrice"], high=data["HighPrice"],
                         low=data["LowPrice"],close=data["ClosePrice"])
                         ])

fig.update_layout(xaxis_rangeslider_visible=False)
fig.show()

# *STRATEGY*

##### Resultados de la primera prueba de trading durante toda toda la nochde (+6h.) con una estrategia de +/- 25SMA   

In [11]:
data = pd.read_csv("../results/strategy_1/strategy_1_raw.csv",index_col="Unnamed: 0")
data.index = pd.to_datetime(data.index)
data.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 21190 entries, 2023-11-04 00:44:56 to 2023-11-04 06:50:55
Data columns (total 3 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   price   21190 non-null  float64
 1   MA_25   21166 non-null  float64
 2   signal  21166 non-null  object 
dtypes: float64(2), object(1)
memory usage: 662.2+ KB


In [17]:
wallet = pd.read_csv("../results/strategy_1/strategy_1_results.csv", index_col="Unnamed: 0")
wallet.index = pd.to_datetime(wallet.index)
wallet

wallet
2023-11-04 00:45:20  100.000000
2023-11-04 00:45:38   99.998703
2023-11-04 00:46:12   99.998703
2023-11-04 00:46:13   99.998674
2023-11-04 00:46:14   99.998674
...                         ...
2023-11-04 06:50:01  103.008440
2023-11-04 06:50:04  103.008410
2023-11-04 06:50:07  103.008410
2023-11-04 06:50:08  103.000686
2023-11-04 06:50:27  103.000686

[2466 rows x 1 columns]

In [23]:
fig = make_subplots(specs=[[{"secondary_y":True}]])

fig.add_trace(
    go.Scatter(
        x=data.index,
        y=np.log10(data["price"]),
        name="Price"
    ),
    secondary_y=False
)

fig.add_trace(
    go.Scatter(
        x=wallet.index,
        y=np.log10(wallet["wallet"]),
        name="wallet"
    ),
    secondary_y=True
)

fig.update_xaxes(title_text="datetime")

fig.update_yaxes(title_text="<b>Price</b> BTCUSDT", secondary_y=False)
fig.update_yaxes(title_text="<b>Wallet</b> wallet", secondary_y=True)

fig.show()

In [65]:


fig = make_subplots(rows=2,cols=2,
                    specs=[[{"secondary_y": True,"colspan":2}, {"secondary_y": True}],
                           [{"secondary_y": True}, {"secondary_y": True}]])

# ========================= Valores nominales =========================

fig.add_trace(
    go.Scatter(
        x=data.index,
        y=data["price"],
        name="Price"
    ),
    row=1,col=1,
    secondary_y=False
)

fig.add_trace(
    go.Scatter(
        x=wallet.index,
        y=wallet["wallet"],
        name="wallet"
    ),
    row=1,col=1,
    secondary_y=True
)

# ======================================================================

# ========================= Crecimiento acumulado =========================

fig.add_trace(
    go.Scatter(
        x=data.index,
        y=((1 + data["price"].pct_change()).cumprod() - 1)*100,
        name="% acum Price"
    ),
    row=2,col=1,
    secondary_y=False
)

fig.add_trace(
    go.Scatter(
        x=wallet.index,
        y=((1 + wallet["wallet"].pct_change()).cumprod() - 1)*100,
        name="% acum wallet"
    ),
    row=2,col=1,
    secondary_y=False
)

# ==========================================================================

# ========================= Crecimiento acumulado =========================

fig.add_trace(
    go.Scatter(
        x=data.index,
        y=data["price"].pct_change()*100,
        name="%Price"
    ),
    row=2,col=2,
    secondary_y=False
)

fig.add_trace(
    go.Scatter(
        x=wallet.index,
        y=wallet["wallet"].pct_change()*100,
        name="%wallet"
    ),
    row=2,col=2,
    secondary_y=False
)

# ==========================================================================



fig.update_layout(legend=dict(
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="right",
        x=1),
    height=900, width=1400,
    margin={'t':20,'l':0,'b':20,'r':0},
    title = "BTCUSDT auto-trade night"
)

#fig.update_xaxes(title_text="datetime")

fig.update_yaxes(title_text="<b>Price</b> BTCUSDT", secondary_y=False, row=1,col=1)
fig.update_yaxes(title_text="<b>Wallet</b> wallet", secondary_y=True, row=1,col=1)
fig.update_yaxes(title_text="<b> % </b> Growth", secondary_y=False, row=2,col=1)


fig.show()